
# Benchmark Evaluation


In this demo, **we will focus on evaluating large language models using a benchmark dataset specific to the task at hand.**

**Learning Objectives:**

*By the end of this demo, you will be able to;*

* Obtain reference/benchmark data set for task-specific LLM evaluation
* Evaluate an LLM's performance on a specific task using task-specific metrics
* Compare relative performance of two LLMs using a benchmark set

In [0]:
%pip install -U -qq databricks-sdk rouge_score evaluate textstat mlflow tiktoken
dbutils.library.restartPython()

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


Before starting the demo, run the provided classroom setup script. This script will define configuration variables necessary for the demo. Execute the following cell:

In [0]:
%run ../Includes/Classroom-Setup-03


The examples and models presented in this course are intended solely for demonstration and educational purposes.
 Please note that the models and prompt examples may sometimes contain offensive, inaccurate, biased, or harmful content.


**Other Conventions:**

Throughout this demo, we'll refer to the object `DA`. This object, provided by Databricks Academy, contains variables such as your username, catalog name, schema name, working directory, and dataset locations. Run the code block below to view these details:

In [0]:
print(f"Username:          {DA.username}")
print(f"Catalog Name:      {DA.catalog_name}")
print(f"Schema Name:       {DA.schema_name}")
print(f"Working Directory: {DA.paths.working_dir}")
print(f"Dataset Location:  {DA.paths.datasets}")

Username:          labuser11003544_1753435669@vocareum.com
Catalog Name:      dbacademy
Schema Name:       labuser11003544_1753435669
Working Directory: /Volumes/dbacademy/ops/labuser11003544_1753435669@vocareum_com
Dataset Location:  NestedNamespace (news='/Volumes/dbacademy_news/v01', arxiv='/Volumes/dbacademy_arxiv/v01')


## Demo Overview

In this demonstration, we will be evaluating the performance of an AI system designed to summarize text.

The text documents that we will be summarizing are a collection of fictional product reviews for grocery products.

The AI system works as follows:

1. Accepts a text document as input
2. Constructs an LLM prompt using few-shot learning to summarize the text
3. Submits the prompt to an LLM for summarization
4. Returns summarized text

See below for an example of the system.

## Step 1: Setup Models to Use

Next, we will setup the model that will be used for evaluation.

We will use **Databricks Claude 3.7 Sonnet** and **Llama 3.3 70B Instruct** for evaluation.

In [0]:
from databricks.sdk.service.serving import ChatMessage
from databricks.sdk import WorkspaceClient

w = WorkspaceClient()

# Define the first model for summarization
def query_summary_system(input: str) -> str:
    messages = [
        {
            "role": "system",
            "content": "You are an assistant that summarizes text. Given a text input, you need to provide a one-sentence summary. You specialize in summarizing reviews of grocery products. Please keep the reviews in first-person perspective if they're originally written in first person. Do not change the sentiment. Do not create a run-on sentence – be concise."
        },
        { 
            "role": "user", 
            "content": input 
        }
    ]
    messages = [ChatMessage.from_dict(message) for message in messages]
    chat_response = w.serving_endpoints.query(
        name="databricks-claude-3-7-sonnet",
        messages=messages,
        temperature=0.1,
        max_tokens=128
    )

    return chat_response.as_dict()["choices"][0]["message"]["content"]

# Define the second model for summarization
def challenger_query_summary_system(input: str) -> str:
    messages = [
        {
            "role": "system",
            "content": "You are an assistant that summarizes text. Given a text input, you need to provide a one-sentence summary. You specialize in summarizing reviews of grocery products. Please keep the reviews in first-person perspective if they're originally written in first person. Do not change the sentiment. Do not create a run-on sentence – be concise."
        },
        { 
            "role": "user", 
            "content": input 
        }
    ]
    messages = [ChatMessage.from_dict(message) for message in messages]
    chat_response = w.serving_endpoints.query(
        name="databricks-meta-llama-3-3-70b-instruct",
        messages=messages,
        temperature=0.1,
        max_tokens=128
    )

    return chat_response.as_dict()["choices"][0]["message"]["content"]

Let's test the models!

In [0]:
query_summary_system(
    "This is the best frozen pizza I've ever had! Sure, it's not the healthiest, but it tasted just like it was delivered from our favorite pizzeria down the street. The cheese browned nicely and fresh tomatoes are a nice touch, too! I would buy it again despite it's high price. If I could change one thing, I'd made it a little healthier – could we get a gluten-free crust option? My son would love that."
)

"I loved this frozen pizza for its authentic pizzeria taste, nicely browned cheese and fresh tomatoes, though I wish they'd offer a gluten-free option despite the high price."

In [0]:
challenger_query_summary_system(
    "This is the best frozen pizza I've ever had! Sure, it's not the healthiest, but it tasted just like it was delivered from our favorite pizzeria down the street. The cheese browned nicely and fresh tomatoes are a nice touch, too! I would buy it again despite it's high price. If I could change one thing, I'd made it a little healthier – could we get a gluten-free crust option? My son would love that."
)

"I think this is the best frozen pizza I've ever had, with a delicious taste similar to a pizzeria's, and I would buy it again despite its high price."

To complete this workflow, we'll focus on the following steps:

1. Obtain a benchmark set for evaluating summarization
2. Compute summarization-specific evaluation metrics using the benchmark set
3. Compare performance with another LLM using the benchmark set and evaluation metrics

## Step 2: Benchmark and Reference Sets

As a reminder, our task-specific evaluation metrics (including ROUGE for summarization) require a benchmark set to compute scores.

There are two types of reference/benchmark sets that we can use:

1. Large, generic benchmark sets commonly used across use cases
2. Domain-specific benchmark sets specific to your use case

For this demo, we'll focus on the former.

### Generic Benchmark Set

First, we'll import a generic benchmark set used for evaluating text summarization.

We'll use the data set used in [Benchmarking Large Language Models for News Summarization](https://arxiv.org/abs/2301.13848) to evaluate how well our LLM solution summarizes general text.

This data set:

* is relatively large in scale at 599 records
* is related to news articles
* contains original text and *author-written* summaries of the original text

**Question:** What is the advantage of using ground-truth summaries that are written by the original author?

In [0]:
import pandas as pd

# Read and display the dataset
eval_data = pd.read_csv(f"{DA.paths.datasets.news}/csv/news-summaries.csv")
display(eval_data)

inputs writer_summary Baltimore's mayor has sacked the US city's police chief, saying his leadership had become a distraction from fighting a "crime surge".

Mayor Stephanie Rawlings-Blake said she was replacing Police Commissioner Anthony Batts with his deputy, Kevin Davis, for an interim period.

The city was rocked by riots in April when a black man died after suffering injuries in police custody.

Six officers were charged over the death of the 25-year-old, Freddie Gray.

Speaking at a news conference on Wednesday, Mayor Rawlings-Blake said Mr Batts had "served this city with distinction" since becoming police chief in October 2012.

But referring to the city's high homicide rate, she said "too many continue to die".

"The focus has been too much on the leadership of the department and not enough on the crime fighting," she told reporters, adding: "We need to get the crime surge under control."

The city has seen a sharp increase in violence since Freddie Gray's death on 19 April, with 155 homicides this year, a 48% increase over the same period last year.

On Tuesday, the police department announced that an outside organisation will review its response to the civil unrest that followed Mr Gray's death.

The US justice department is also conducting a civil rights review of the Baltimore force and Mr Batts has been criticised by the city's police union.

Earlier on Wednesday, the union released its report into the police handling of the rioting.

It said officers had complained "that they lacked basic riot equipment, training, and, as events unfolded, direction from leadership".

The report also said "officers repeatedly expressed concern that the passive response to the civil unrest had allowed the disorder to grow into full scale rioting".

Recent events had "placed attention on police leadership", Ms Rawlings-Blake said, but denied her decision was influenced by the union report.

Mr Davis, who is taking over immediately as interim police chief, praised his "friend" Mr Batts and said he was a "true reform commissioner".

Mayor Rawlings-Blake said Mr Davis would "bring accountability to police, hold officers who act out of line accountable for their actions". The mayor of Baltimore fired the police chief and replaced him with his deputy. According to the mayor, crime in the city was unacceptable. Riots in the city after a man died in police custody and a surge in homicide rates were cited as reasons for the firing. Western Sahara has welcomed Morocco's readmission to the African Union, 32 years after members refused to withdraw support for the territory's independence.

It was a "good opportunity" and "a chance to work together," a top Western Sahara official told the BBC.

Morocco controls two-thirds of Western Sahara and sees it as part of its historic territory.

However some, including the UN, see Western Sahara as Africa's last colony.

Africa Live: More on this and other stories

Find out more about Western Sahara

A referendum was promised in 1991 but never carried out due to wrangling over who was eligible to vote.

Thousands of Sahrawi refugees still live in refugee camps in Algeria - some have been there for 40 years.

It is not clear what happens next but Western Sahara is hopeful that a committee set up by the AU will address the issues that both sides have raised.

Some AU delegates said that it would be easier to resolve the issue with Morocco inside the AU.

Sidi Mohammed, a Western Sahara official, told the BBC that Morocco's return to the AU means that it would now be expected to put "in practice decisions taken by the AU with regard to a referendum in Western Sahara".

Mr Mohammed dismissed the suggestion that Morocco would now seek to get the AU to change its position, saying that the no country could unilaterally change the AU fundamental agreement, saying it opposed colonisation.

In his speech at the AU summit, King Mohammed VI of Morocco said the readmission was not meant to divide the continental b

## Step 3: Compute the ROUGE Evaluation Metric

Next, we will want to compute our ROUGE-N metric to understand how well our system summarizes grocery generic text using the benchmark dataset.

We can compute the ROUGE metric (among others) using MLflow's new LLM evaluation capabilities. MLflow LLM evaluation includes default collections of metrics for pre-selected tasks, e.g, “question-answering” or "text-summarization" (our case). Depending on the LLM use case that you are evaluating, these pre-defined collections can greatly simplify the process of running evaluations.

The `mlflow.evaluate` function accepts the following parameters for this use case:

* An LLM model
* Reference data for evaluation (our benchmark set)
* Column with ground truth data
* The model/task type (e.g. `"text-summarization"`)

**Note:** The `text-summarization` type will automatically compute ROUGE-related metrics. For some metrics, additional library installs will be needed – you can see the requirements in the printed output.

In [0]:
# A custom function to iterate through our eval DF
def query_iteration(inputs):
    answers = []

    for index, row in inputs.iterrows():
        completion = query_summary_system(row["inputs"])
        answers.append(completion)

    return answers

# Test query_iteration function – it needs to return a list of output strings
query_iteration(eval_data.head())

["Baltimore's mayor fired the city's police chief, replacing him with his deputy, citing that his leadership had become a distraction from addressing the 48% increase in homicides amid ongoing tensions following Freddie Gray's death in police custody.",
 "Western Sahara officials welcomed Morocco's readmission to the African Union after 32 years, viewing it as an opportunity to work together despite ongoing disputes over Western Sahara's independence and Morocco's control of two-thirds of the territory.",
 'England flanker James Haskell shared an Instagram photo of himself dressed as Iron Man to celebrate the release of Avengers: Age of Ultron.',
 'UK manufacturing activity contracted in April for the first time in three years due to soft domestic demand, falling overseas business, and uncertainty ahead of the EU referendum, potentially acting as a drag on the economy.',
 'A mother-of-six lost over seven stone after being mortified when a child on a bus asked if she was pregnant, inspi

In [0]:
import mlflow

# MLflow's `evaluate` with a custom function
results = mlflow.evaluate(
    query_iteration,                      # iterative function from above
    eval_data.head(50),                   # limiting for speed
    targets="writer_summary",             # column with expected or "good" output
    model_type="text-summarization"       # type of model or task
)

/local_disk0/.ephemeral_nfs/envs/pythonEnv-4f79d6b3-a729-4b08-a63b-39f17c5fb17b/lib/python3.10/site-packages/mlflow/models/evaluation/deprecated.py:13: FutureWarning: The `mlflow.evaluate` API has been deprecated as of MLflow 3.0.0. Please use these new alternatives:

 - For traditional ML or deep learning models: Use `mlflow.models.evaluate`, which maintains full compatibility with the original `mlflow.evaluate` API.

 - For LLMs or GenAI applications: Use the new `mlflow.genai.evaluate` API, which offers enhanced features specifically designed for evaluating LLMs and GenAI applications.

  warnings.warn(
2025/07/25 09:44:00 INFO mlflow.models.evaluation.evaluators.default: Computing model predictions.
2025/07/25 09:45:40 INFO mlflow.models.evaluation.default_evaluator: Testing metrics on first row...
2025/07/25 09:45:42 WARNING mlflow.metrics.metric_definitions: Failed to load 'toxicity' metric (error: ImportError("To be able to use evaluate-measurement/toxicity, you need to install 

We can view the results for individual records by subsetting the handy `.tables` object.

Notice all of the different versions of the ROUGE metric. These are calculated using the HuggingFace `evaluator` library, and the metrics are detailed [here](https://huggingface.co/spaces/evaluate-metric/rouge).

In summary, the descriptions of each metric are below:

* "rouge1": unigram (1-gram) based scoring
* "rouge2": bigram (2-gram) based scoring
* "rougeL": Longest common subsequence based scoring.
* "rougeLSum": splits text using "\n"

In [0]:
display(results.tables["eval_results_table"].head(10))

inputs writer_summary outputs token_count flesch_kincaid_grade_level/v1/score ari_grade_level/v1/score rouge1/v1/score rouge2/v1/score rougeL/v1/score rougeLsum/v1/score Baltimore's mayor has sacked the US city's police chief, saying his leadership had become a distraction from fighting a "crime surge".

Mayor Stephanie Rawlings-Blake said she was replacing Police Commissioner Anthony Batts with his deputy, Kevin Davis, for an interim period.

The city was rocked by riots in April when a black man died after suffering injuries in police custody.

Six officers were charged over the death of the 25-year-old, Freddie Gray.

Speaking at a news conference on Wednesday, Mayor Rawlings-Blake said Mr Batts had "served this city with distinction" since becoming police chief in October 2012.

But referring to the city's high homicide rate, she said "too many continue to die".

"The focus has been too much on the leadership of the department and not enough on the crime fighting," she told reporters, adding: "We need to get the crime surge under control."

The city has seen a sharp increase in violence since Freddie Gray's death on 19 April, with 155 homicides this year, a 48% increase over the same period last year.

On Tuesday, the police department announced that an outside organisation will review its response to the civil unrest that followed Mr Gray's death.

The US justice department is also conducting a civil rights review of the Baltimore force and Mr Batts has been criticised by the city's police union.

Earlier on Wednesday, the union released its report into the police handling of the rioting.

It said officers had complained "that they lacked basic riot equipment, training, and, as events unfolded, direction from leadership".

The report also said "officers repeatedly expressed concern that the passive response to the civil unrest had allowed the disorder to grow into full scale rioting".

Recent events had "placed attention on police leadership", Ms Rawlings-Blake said, but denied her decision was influenced by the union report.

Mr Davis, who is taking over immediately as interim police chief, praised his "friend" Mr Batts and said he was a "true reform commissioner".

Mayor Rawlings-Blake said Mr Davis would "bring accountability to police, hold officers who act out of line accountable for their actions". The mayor of Baltimore fired the police chief and replaced him with his deputy. According to the mayor, crime in the city was unacceptable. Riots in the city after a man died in police custody and a surge in homicide rates were cited as reasons for the firing. Baltimore's mayor fired the city's police chief, citing his leadership as a distraction from addressing the 48% increase in homicides, and appointed his deputy as interim commissioner to focus on crime fighting rather than departmental leadership. 45 21.0666666667 24.3066666667 0.3720930233 0.0952380952 0.2325581395 0.2325581395 Western Sahara has welcomed Morocco's readmission to the African Union, 32 years after members refused to withdraw support for the territory's independence.

It was a "good opportunity" and "a chance to work together," a top Western Sahara official told the BBC.

Morocco controls two-thirds of Western Sahara and sees it as part of its historic territory.

However some, including the UN, see Western Sahara as Africa's last colony.

Africa Live: More on this and other stories

Find out more about Western Sahara

A referendum was promised in 1991 but never carried out due to wrangling over who was eligible to vote.

Thousands of Sahrawi refugees still live in refugee camps in Algeria - some have been there for 40 years.

It is not clear what happens next but Western Sahara is hopeful that a committee set up by the AU will address the issues that both sides have raised.

Some AU delegates said that it would be easier to resolve the issue with Morocco inside the AU.

Sidi Mohammed, a Western Sahara official, told the BBC that Morocco's return to 

And we can view summarized (mean, variance, etc.) model-level (rather than record-level) results with the following:

In [0]:
results.metrics

{'flesch_kincaid_grade_level/v1/mean': 19.03158332053003,
 'flesch_kincaid_grade_level/v1/variance': 9.920752976135542,
 'flesch_kincaid_grade_level/v1/p90': 23.55196951219512,
 'ari_grade_level/v1/mean': 22.203561632847464,
 'ari_grade_level/v1/variance': 13.054990385022968,
 'ari_grade_level/v1/p90': 27.252891447368427,
 'rouge1/v1/mean': 0.36465009596853387,
 'rouge1/v1/variance': 0.007300583160622519,
 'rouge1/v1/p90': 0.5,
 'rouge2/v1/mean': 0.14686018524751876,
 'rouge2/v1/variance': 0.005853832207442289,
 'rouge2/v1/p90': 0.25925696594427244,
 'rougeL/v1/mean': 0.2523175808786251,
 'rougeL/v1/variance': 0.007047457459383682,
 'rougeL/v1/p90': 0.35299782541161856,
 'rougeLsum/v1/mean': 0.2523175808786251,
 'rougeLsum/v1/variance': 0.007047457459383682,
 'rougeLsum/v1/p90': 0.35299782541161856}

We are also able to review the results in the MLflow Experiment Tracking UI.

### What does good look like?

The ROUGE metrics range between 0 and 1 – where 0 indicates extremely dissimilar text and 1 indicates extremely similar text. However, our interpretation of what is "good" is usually going to be use-case specific. We don't always want a ROUGE score close to 1 because it's likely not reducing the text size too much.

To explore what "good" looks like, let's review a couple of our examples.

In [0]:
import pandas as pd
display(
    pd.DataFrame(
        results.tables["eval_results_table"]
    ).loc[0:1, ["inputs", "outputs", "rouge1/v1/score"]]
)

inputs outputs rouge1/v1/score Baltimore's mayor has sacked the US city's police chief, saying his leadership had become a distraction from fighting a "crime surge".

Mayor Stephanie Rawlings-Blake said she was replacing Police Commissioner Anthony Batts with his deputy, Kevin Davis, for an interim period.

The city was rocked by riots in April when a black man died after suffering injuries in police custody.

Six officers were charged over the death of the 25-year-old, Freddie Gray.

Speaking at a news conference on Wednesday, Mayor Rawlings-Blake said Mr Batts had "served this city with distinction" since becoming police chief in October 2012.

But referring to the city's high homicide rate, she said "too many continue to die".

"The focus has been too much on the leadership of the department and not enough on the crime fighting," she told reporters, adding: "We need to get the crime surge under control."

The city has seen a sharp increase in violence since Freddie Gray's death on 19 April, with 155 homicides this year, a 48% increase over the same period last year.

On Tuesday, the police department announced that an outside organisation will review its response to the civil unrest that followed Mr Gray's death.

The US justice department is also conducting a civil rights review of the Baltimore force and Mr Batts has been criticised by the city's police union.

Earlier on Wednesday, the union released its report into the police handling of the rioting.

It said officers had complained "that they lacked basic riot equipment, training, and, as events unfolded, direction from leadership".

The report also said "officers repeatedly expressed concern that the passive response to the civil unrest had allowed the disorder to grow into full scale rioting".

Recent events had "placed attention on police leadership", Ms Rawlings-Blake said, but denied her decision was influenced by the union report.

Mr Davis, who is taking over immediately as interim police chief, praised his "friend" Mr Batts and said he was a "true reform commissioner".

Mayor Rawlings-Blake said Mr Davis would "bring accountability to police, hold officers who act out of line accountable for their actions". Baltimore's mayor fired the city's police chief, citing his leadership as a distraction from addressing the 48% increase in homicides, and appointed his deputy as interim commissioner to focus on crime fighting rather than departmental leadership. 0.3720930233 Western Sahara has welcomed Morocco's readmission to the African Union, 32 years after members refused to withdraw support for the territory's independence.

It was a "good opportunity" and "a chance to work together," a top Western Sahara official told the BBC.

Morocco controls two-thirds of Western Sahara and sees it as part of its historic territory.

However some, including the UN, see Western Sahara as Africa's last colony.

Africa Live: More on this and other stories

Find out more about Western Sahara

A referendum was promised in 1991 but never carried out due to wrangling over who was eligible to vote.

Thousands of Sahrawi refugees still live in refugee camps in Algeria - some have been there for 40 years.

It is not clear what happens next but Western Sahara is hopeful that a committee set up by the AU will address the issues that both sides have raised.

Some AU delegates said that it would be easier to resolve the issue with Morocco inside the AU.

Sidi Mohammed, a Western Sahara official, told the BBC that Morocco's return to the AU means that it would now be expected to put "in practice decisions taken by the AU with regard to a referendum in Western Sahara".

Mr Mohammed dismissed the suggestion that Morocco would now seek to get the AU to change its position, saying that the no country could unilaterally change the AU fundamental agreement, saying it opposed colonisation.

In his speech at the AU summit, King Mohammed VI of Morocco said the readmission was not meant to divide the cont

**Discussion Questions:**
1. How do you interpret the ROUGE-1 score?
2. Do the scores reflect the summarization that you think is best?

## Step 4: Comparing LLM Performance

In practice, we will frequently be comparing LLMs (or larger AI systems) against one another when determining which is the best for our use case. As a result of this, it's important to become familiar with comparing these solutions.

In the below cell, we demonstrate computing the same metrics using the same reference dataset – but this time, we're summarizing using a system that utilizes a different LLM.

**Note:** This time, we're going to read our reference dataset from Delta.

In [0]:
# A compare custom function to iterate through our eval DF
def challenger_query_iteration(inputs):
    answers = []

    for index, row in inputs.iterrows():
        completion = challenger_query_summary_system(row["inputs"])
        answers.append(completion)

    return answers

# Compute challenger results
challenger_results = mlflow.evaluate(
    challenger_query_iteration,           # iterative function from above
    eval_data.head(50),
    targets="writer_summary",             # column with expected or "good" output
    model_type="text-summarization"       # type of model or task
)

/local_disk0/.ephemeral_nfs/envs/pythonEnv-4f79d6b3-a729-4b08-a63b-39f17c5fb17b/lib/python3.10/site-packages/mlflow/models/evaluation/deprecated.py:13: FutureWarning: The `mlflow.evaluate` API has been deprecated as of MLflow 3.0.0. Please use these new alternatives:

 - For traditional ML or deep learning models: Use `mlflow.models.evaluate`, which maintains full compatibility with the original `mlflow.evaluate` API.

 - For LLMs or GenAI applications: Use the new `mlflow.genai.evaluate` API, which offers enhanced features specifically designed for evaluating LLMs and GenAI applications.

  warnings.warn(
2025/07/25 09:46:02 INFO mlflow.models.evaluation.evaluators.default: Computing model predictions.
2025/07/25 09:46:40 INFO mlflow.models.evaluation.default_evaluator: Testing metrics on first row...
2025/07/25 09:46:41 WARNING mlflow.metrics.metric_definitions: Failed to load 'toxicity' metric (error: ImportError("To be able to use evaluate-measurement/toxicity, you need to install 

Let's take a look at our model-level results.

In [0]:
challenger_results.metrics

{'flesch_kincaid_grade_level/v1/mean': 17.843583371921884,
 'flesch_kincaid_grade_level/v1/variance': 9.53804337086556,
 'flesch_kincaid_grade_level/v1/p90': 21.699272727272735,
 'ari_grade_level/v1/mean': 20.385179164547687,
 'ari_grade_level/v1/variance': 14.55051111110084,
 'ari_grade_level/v1/p90': 25.043977272727272,
 'rouge1/v1/mean': 0.33090330392427647,
 'rouge1/v1/variance': 0.00612536675930271,
 'rouge1/v1/p90': 0.42875226039783004,
 'rouge2/v1/mean': 0.11782701899335928,
 'rouge2/v1/variance': 0.0049505816216773016,
 'rouge2/v1/p90': 0.22854545454545458,
 'rougeL/v1/mean': 0.21761264549798823,
 'rougeL/v1/variance': 0.004764221727284637,
 'rougeL/v1/p90': 0.2891666666666667,
 'rougeLsum/v1/mean': 0.21761264549798823,
 'rougeLsum/v1/variance': 0.004764221727284637,
 'rougeLsum/v1/p90': 0.2891666666666667}

And let's compare in the MLflow UI, looking at the experiment's **Chart** tab.

**Note:** We can filter specifically to ROUGE metrics.

### What about other tasks/metrics?

The `mlflow` library contains [a number of LLM task evaluation tools](https://mlflow.org/docs/latest/python_api/mlflow.html#mlflow.evaluate) that we can use in our workflows.